Partimos importando las librerías necesarias. Instalaremos Plotly, una librería muy amigable para visualizaciones interactivas.

In [19]:
%%capture
#pip install plotly

In [20]:
import pandas as pd
import numpy as np
import plotly.express as px
import matplotlib.pyplot as plt

Leemos los datos y les damos formato adecuado a las fechas. Agregamos una columna llamada count con un 1 en cada fila. Esto nos permitirá luego agrupar el Dataframe y saber cuantas filas entran en cada grupo. 

In [21]:
df = pd.read_csv('dataset_SCL.csv')
df['Fecha-I'] = pd.to_datetime(df['Fecha-I'], format='%Y-%m-%d %H:%M:%S')
df['Fecha-O'] = pd.to_datetime(df['Fecha-O'], format='%Y-%m-%d %H:%M:%S')
df['Count'] = 1
print(f'Dimensiones base de datos: {df.shape}')
df.head()

Dimensiones base de datos: (68206, 19)


/var/folders/l0/cs9rz_356vq87jr_ptnhp2qr0000gn/T/ipykernel_74486/2804793220.py:1: DtypeWarning:

Columns (1,6) have mixed types. Specify dtype option on import or set low_memory=False.



Fecha-I Vlo-I Ori-I Des-I Emp-I             Fecha-O Vlo-O Ori-O  \
0 2017-01-01 23:30:00   226  SCEL  KMIA   AAL 2017-01-01 23:33:00   226  SCEL   
1 2017-01-02 23:30:00   226  SCEL  KMIA   AAL 2017-01-02 23:39:00   226  SCEL   
2 2017-01-03 23:30:00   226  SCEL  KMIA   AAL 2017-01-03 23:39:00   226  SCEL   
3 2017-01-04 23:30:00   226  SCEL  KMIA   AAL 2017-01-04 23:33:00   226  SCEL   
4 2017-01-05 23:30:00   226  SCEL  KMIA   AAL 2017-01-05 23:28:00   226  SCEL   

  Des-O Emp-O  DIA  MES   AÑO     DIANOM TIPOVUELO              OPERA  \
0  KMIA   AAL    1    1  2017    Domingo         I  American Airlines   
1  KMIA   AAL    2    1  2017      Lunes         I  American Airlines   
2  KMIA   AAL    3    1  2017     Martes         I  American Airlines   
3  KMIA   AAL    4    1  2017  Miercoles         I  American Airlines   
4  KMIA   AAL    5    1  2017     Jueves         I  American Airlines   

   SIGLAORI SIGLADES  Count  
0  Santiago    Miami      1  
1  Santiago    Miami      1  
2  Santiago    Miami      1  
3  Santiago    Miami      1  
4  Santiago    Miami      1

## Análisis exploratorio

Generamos una serie de simples visualizaciones para explorar los datos

Notamos que hay un buen balance entre vuelos nacionales e internacionales. 

In [22]:
fig = px.pie(df, names='TIPOVUELO', title='Distribución de tipos de vuelo')
fig.show()

También hay un balanance entre los días de operación de los vuelos. Lunes, jueves y viernes son los días donde más se vuela. El sábado es el día que menos.

In [23]:
df['DIANOM'] = pd.Categorical(df['DIANOM'], categories=['Lunes', 'Martes', 'Miercoles', 'Jueves', 'Viernes', 'Sabado', 'Domingo'], ordered=True)
px.histogram(df['DIANOM'])

Ahora vemos desde donde inician y terminan los vuelos. Todos parten desde Santiago, tal como se esperaba. Si apretamos el botón de SIGLAORI en la derecha podemos observar mejor la distribución de los destinos. Buenos Aires, Antofagasta, Calama y Lima son los lugares hacia donde se dirigen más vuelos. Notamos también una serie de localidades (aproximadamente 50% de los destinos) que tienen menos de 500 vuelos. Es importante ser cuidadoso con ellos en el análisis posterior ya que eventualmente podrían pocos ejemplos tener un impacto muy grande en el modelo. 

In [24]:
px.histogram(df[['SIGLADES','SIGLAORI']])

Notamos que la mayoría de los vuelos los opera LATAM o SKY (aproximadamente 90% de los vuelos totales).Sin embargo, al desglosar por nacionales o internacionales notamos que la distribución cambia bastante. En el mercado nacional aparece LATAM y SKY con fuerza. Latin American wings y jetsmart apenas suman unos 1500 vuelos. No hay mas operadores del mercado nacional. Del internacional LATAM nuevamente es el principal, sin emabargo ahora aparecen muchos más "competidores". LATAM tiene el 64% de los vuelos nacionales y el 54% de los nacionales.

In [25]:
px.histogram(df['OPERA'])

In [26]:
fig = px.histogram(df, x='OPERA', color='TIPOVUELO', title='Número de vuelos por aerolínea y tipo de vuelo')
fig.show()

In [27]:
latam_int = df[(df['OPERA'] == 'Grupo LATAM') & (df['TIPOVUELO'] == 'I')].shape[0] / df[df['TIPOVUELO'] == 'I'].shape[0]
latam_na = df[(df['OPERA'] == 'Grupo LATAM') & (df['TIPOVUELO'] == 'N')].shape[0] / df[df['TIPOVUELO'] == 'N'].shape[0]
print(f'Porcentaje de vuelos LATAM internacional: {round(latam_int*100, 3)}%')
print(f'Porcentaje de vuelos LATAM acional: {round(latam_na*100, 3)}%')

Porcentaje de vuelos LATAM internacional: 54.894%
Porcentaje de vuelos LATAM acional: 64.229%


In [28]:
dict_fechas_dianom = pd.Series(df['DIANOM'].values, index=df['Fecha-I'].dt.date).to_dict()
df_dates = df.groupby(df['Fecha-I'].dt.date).sum().reset_index()
df_dates['DIANOM'] = df['Fecha-I'].dt.date.apply(lambda x: dict_fechas_dianom[x])

Ahora nos fijamos en la distribución temporal de los vuelos. Primero vemos que la media es de 186 vuelos al día. También vemos una estacionalidad muy marcada. Desde marzo a junio la cantidad de vuelos diarios es muy baja. A partir de julio la cantidad de vuelos vuelve a subir (seguramente influenciado por el inicio de las vacaciones de invierno). Vuelve a verse un aumento sostenido hasta marzo 2018.

In [29]:
fig = px.line(df_dates, x="Fecha-I",  y='Count', title=f"<b> Cantidad de viajes en el tiempo</b>", markers=True, width=1000, height=600)
last_week_mean = df_dates['Count'].mean()
fig.add_hline(y=last_week_mean, line_dash='dash', line_color='red', annotation_text=f'Mean: {last_week_mean:.2f}', annotation_position='top right')
fig.show()

En resumen del análisis exploratorio, se ve que existen variables que parecen estar muy bien distribuidas entre todas sus alternativas, tales como los días de semana de operación y si el destino es nacional o internacional. Por otra parte, existen variablaes que tienen concentraciones muy altas en pocos elementos, tales como los destinos y operadores. También se observa una fuerte estacionalidad en la cantidad de vuelos. 

## Nuevas columnas

### Temporada alta

In [30]:
def temporada_alta(date_):
    date_ = date_.date() 
    if (date_ >= pd.to_datetime('15-12-2016').date()) and ( date_ <= pd.to_datetime('03-03-2017').date()):
        return 1
    elif (date_ >= pd.to_datetime('15-12-2017').date()) and ( date_ <= pd.to_datetime('03-03-2018').date()):
        return 1
    elif (date_ >= pd.to_datetime('15-07-2017').date()) and ( date_ <= pd.to_datetime('31-07-2017').date()):
        return 1 
    elif (date_ >= pd.to_datetime('11-09-2017').date()) and ( date_ <= pd.to_datetime('30-09-2017').date()):
        return 1
    return 0


df['Temporada alta'] =  df['Fecha-I'].apply(lambda date_: temporada_alta(date_))

/var/folders/l0/cs9rz_356vq87jr_ptnhp2qr0000gn/T/ipykernel_74486/1551884746.py:3: UserWarning:

Parsing '15-12-2016' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.

/var/folders/l0/cs9rz_356vq87jr_ptnhp2qr0000gn/T/ipykernel_74486/1551884746.py:5: UserWarning:

Parsing '15-12-2017' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.

/var/folders/l0/cs9rz_356vq87jr_ptnhp2qr0000gn/T/ipykernel_74486/1551884746.py:7: UserWarning:

Parsing '15-07-2017' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.

/var/folders/l0/cs9rz_356vq87jr_ptnhp2qr0000gn/T/ipykernel_74486/1551884746.py:7: UserWarning:

Parsing '31-07-2017' in DD/MM/YYYY format. Provide format or specify infer_datetime_format=True for consistent parsing.

/var/folders/l0/cs9rz_356vq87jr_ptnhp2qr0000gn/T/ipykernel_74486/1551884746.py:9: UserWarning:

Parsing '30-09-2017' in DD/MM/YYYY f

Revisamos que el criterio se aplique correctamente visualizando las fechas de temporada alta.

In [31]:
dict_fechas_temp_a = pd.Series(df['Temporada alta'].values, index=df['Fecha-I'].dt.date).to_dict()
df_dates = df.groupby(df['Fecha-I'].dt.date).sum().reset_index()
df_dates['Temporada alta'] = df_dates['Fecha-I'].apply(lambda x: dict_fechas_temp_a[x])


fig = px.line(df_dates, x="Fecha-I",  y='Count',color='Temporada alta', title=f"<b> Cantidad de viajes en el tiempo</b>", markers=True, width=1000, height=600)
fig.show()

### Diferencia en minutos

In [32]:
df['Diferencia en minutos'] = (df['Fecha-O'] - df['Fecha-I']).astype('timedelta64[m]')

### Atraso menor

In [33]:
def atraso_menor(minutes):
    if minutes > 0 and minutes < 15:
        return 1
    return 0
df['Atraso menor'] = df['Diferencia en minutos'].apply(lambda minutes: atraso_menor(minutes))
df[['Diferencia en minutos', 'Atraso menor']].head()

Diferencia en minutos  Atraso menor
0                    3.0             1
1                    9.0             1
2                    9.0             1
3                    3.0             1
4                   -2.0             0

### Periodo día

In [34]:
def periodo_dia(date_):
    hora = date_.hour
    if hora >= 5 and hora < 12:
        return 'Mañana'
    elif hora >= 12 and hora < 19:
        return 'Tarde'
    else:
        return 'Noche'

df['Periodo día'] =  df['Fecha-I'].apply(lambda date_: periodo_dia(date_))

In [35]:
df[['Fecha-I', 'Periodo día']]

Fecha-I Periodo día
0     2017-01-01 23:30:00       Noche
1     2017-01-02 23:30:00       Noche
2     2017-01-03 23:30:00       Noche
3     2017-01-04 23:30:00       Noche
4     2017-01-05 23:30:00       Noche
...                   ...         ...
68201 2017-12-22 14:55:00       Tarde
68202 2017-12-25 14:55:00       Tarde
68203 2017-12-27 14:55:00       Tarde
68204 2017-12-29 14:55:00       Tarde
68205 2017-12-31 14:55:00       Tarde

[68206 rows x 2 columns]

In [36]:
df.to_csv('synthetic_features.csv')